In [3]:
import geopandas as gpd
import pandas as pd
import geodatasets as gds
import folium
import branca.colormap as cm
from folium import plugins

# prompt user to enter file name
file = input("Enter File Name: ")

# read file
gdf = gpd.read_file(file)

# use folium.map to create a map and center it using latitude and longitude coordinates
map = folium.Map(location=[34.2, -112], zoom_start=6.5) # (arizona)

# convert the district column to numeric (if needed for current congressional district data)
# gdf["CD118FP"] = pd.to_numeric(gdf["CD118FP"], errors='coerce')

# create colormap to display on the map
minDis = gdf["District"].min()
maxDis = gdf["District"].max()
colormap = cm.LinearColormap(
    colors=[
            '#2729de','#a28b9a','#c09343','#3eb62c','#7cc8f8','#4A5C64','#4b9276','#d96bab','#F9A78F','#b26e13',
            '#001bff','#99A8AF','#016b2d','#f2fa20','#9376bb','#16d61e','#c23ba8','#00f3ff','#1169ec','#d40cc8',
            '#d9a892','#22d624','#cdcbdf','#6c862a','#960c88','#d91830','#f41563','#434099','#33eb02','#f49eaf',
            '#8b492a','#8a6de4','#9bbb2d','#12e440','#8f965f','#77c644','#451d1e','#9761e1','#3d24e5','#346b07',
            '#e8a6a3','#621b43','#ff5900','#338b03','#0a1c1f','#f36440','#d0f5a0','#cc0bdd','#b47a97','#F3801B',
            '#b6354a','#a5a3df'
            ],
    vmin=minDis,
    vmax=maxDis,
    caption='District'
)

# add a caption to the colormap
colormap.caption = "District"

# option to fullscreen
plugins.Fullscreen(
    position='topleft',
    title='Expand',
    title_cancel='Exit',
).add_to(map)

# create a style function for the map that fills in each district with a color based on each district, starting from district 1 up to all districts in that state
def style_function(feature):
    colorDist = colormap(feature['properties']['District'])
    return {
        "color": 'black',
        "weight": 1,
        "fillOpacity": 0.5,
        "fillColor": colorDist,
    }

# show details when hovering over a district on the map
tooltip = folium.GeoJsonTooltip(
    fields=["District", "C_TOT22"],
    aliases=["District:", "Population:"],
    labels=True,
    style="""
        border-radius: 10%/50%;
        border: 2px solid red;
        color: blue;
"""
)

# use folium to display district boundaries on the map
folium.GeoJson(
    gdf,
    style_function=style_function,
    tooltip=tooltip,
).add_to(map)

# add the colormap to the map
colormap.add_to(map)

# show the map
map




In [6]:
# combining data based on population and district
import geopandas as gpd

# Load the data from the geodatasets package
df = gpd.read_file("test_map")

# use dissolve to group the data by the 'District' column and aggfunc to sum the population column
grouped = df.dissolve(by='District', 
                      aggfunc={
                          "C_TOT22": "sum",
                      })


# save the grouped data to a new shapefile
grouped.to_file("az_districts_dissolved")
df


GEOID20                                          NAME    STATE  \
0     04021941402   Census Tract 9414.02, Pinal County, Arizona  Arizona   
1     04021002107     Census Tract 21.07, Pinal County, Arizona  Arizona   
2     04021000217      Census Tract 2.17, Pinal County, Arizona  Arizona   
3     04021001714     Census Tract 17.14, Pinal County, Arizona  Arizona   
4     04021002005     Census Tract 20.05, Pinal County, Arizona  Arizona   
...           ...                                           ...      ...   
1760  04015950602  Census Tract 9506.02, Mohave County, Arizona  Arizona   
1761  04015955002  Census Tract 9550.02, Mohave County, Arizona  Arizona   
1762  04015950601  Census Tract 9506.01, Mohave County, Arizona  Arizona   
1763  04015950603  Census Tract 9506.03, Mohave County, Arizona  Arizona   
1764  04015951404  Census Tract 9514.04, Mohave County, Arizona  Arizona   

             COUNTY STATEFP COUNTYFP TRACTCE  C_TOT22  CTOTMOE  C_NHS22  ...  \
0      Pinal County      04      021    9414     2150    547.0     1145  ...   
1      Pinal County      04      021    0021     3850    788.0     3045  ...   
2      Pinal County      04      021    0002     5970    914.0     4410  ...   
3      Pinal County      04      021    0017     5080   1302.0     2515  ...   
4      Pinal County      04      021    0020     6095    412.0     4035  ...   
...             ...     ...      ...     ...      ...      ...      ...  ...   
1760  Mohave County      04      015    9506     2370    457.0     2165  ...   
1761  Mohave County      04      015    9550     3270   1068.0     2380  ...   
1762  Mohave County      04      015    9506     2995    373.0     2425  ...   
1763  Mohave County      04      015    9506     2845    445.0     2725  ...   
1764  Mohave County      04      015    9514     1660    295.0     1380  ...   

      CVAPHSPMOE  CVAP_AIA22  CVAPAIAMOE  CVAP_ASN22  CVAPASNMOE  CVAP_BLK22  \
0          246.0         430      220.92           0       19.80          75   
1          160.0         165      175.33          25       48.08           0   
2          375.0         130      193.87           0       26.87          20   
3          661.0          85       75.95          45       52.55         760   
4          381.0         299      158.83          65       71.85        1074   
...          ...         ...         ...         ...         ...         ...   
1760       125.0           0       24.25          20       34.93          15   
1761       354.0         154       70.01           0       19.80          29   
1762       198.0          80       66.04          30       50.00           0   
1763        85.0         400      270.48           0       19.80           0   
1764       148.0          40       64.13           4       19.10          29   

      CVAPBLKMOE  District  GEOID  \
0          85.33         4      0   
1          24.25         1      1   
2          52.41         9      2   
3         300.64         4      3   
4         260.84         4      4   
...          ...       ...    ...   
1760       33.48         7   1760   
1761       33.44         4   1761   
1762       24.25         7   1762   
1763       24.25         7   1763   
1764       48.55         7   1764   

                                               geometry  
0     POLYGON ((-112.20362 32.51291, -112.20362 32.5...  
1     POLYGON ((-111.79264 32.51290, -111.79262 32.5...  
2     POLYGON ((-111.56337 33.29421, -111.56337 33.2...  
3     POLYGON ((-112.04808 33.01467, -112.04808 33.0...  
4     POLYGON ((-111.56771 32.81759, -111.56771 32.8...  
...                                                 ...  
1760  POLYGON ((-114.28911 35.21207, -114.28911 35.2...  
1761  POLYGON ((-114.63027 34.86599, -114.63018 34.8...  
1762  POLYGON ((-114.41216 35.17994, -114.41215 35.1...  
1763  POLYGON ((-114.27550 35.22889, -114.27492 35.2...  
1764  POLYGON ((-114.58201 35.12657, -114.58192 35.1...  

[1765 rows x 74 columns]